<div style="width: 100%; overflow: hidden;">
    <div style="width: 150px; float: left;"> <img src="data/D4Sci_logo_ball.png" alt="Data For Science, Inc" align="left" border="0"> </div>
    <div style="float: left; margin-left: 10px;"> <h1>LangChain for Generative AI</h1>
<h1>Generative Models</h1>
        <p>Bruno Gonçalves<br/>
        <a href="http://www.data4sci.com/">www.data4sci.com</a><br/>
            @bgoncalves, @data4sci</p></div>
</div>

In [1]:
from collections import Counter
from pprint import pprint
import os

import pandas as pd
import numpy as np
import matplotlib.pyplot as plt 

from IPython.display import Image

import requests
import shutil

import openai
from openai import OpenAI

import transformers
from transformers import pipeline
from transformers import set_seed
set_seed(42) # Set the seed to get reproducible results

from tqdm.notebook import tqdm

import watermark

%load_ext watermark
%matplotlib inline

We start by print out the versions of the libraries we're using for future reference

In [2]:
%watermark -n -v -m -g -iv

Python implementation: CPython
Python version       : 3.11.7
IPython version      : 8.12.3

Compiler    : Clang 14.0.6 
OS          : Darwin
Release     : 23.6.0
Machine     : arm64
Processor   : arm
CPU cores   : 16
Architecture: 64bit

Git hash: 5f98e46f7abc79011d7877a17645c79f3e7672ab

numpy       : 1.26.4
transformers: 4.41.1
matplotlib  : 3.8.0
requests    : 2.32.2
pandas      : 1.5.3
watermark   : 2.4.3
openai      : 1.30.5



Load default figure style

In [3]:
plt.style.use('./d4sci.mplstyle')

## OpenAI

In [4]:
client = OpenAI()

The recommended model for exploration is `gpt-3.5-turbo`, so we'll stick with it for now. The basic setup is relatively straightforward:

### Simple interaction

In [5]:
response = client.chat.completions.create(
  model="gpt-3.5-turbo",
  messages=[
        {
            "role": "user", 
            "content": "What was Superman's weakness?"
        },
    ]
)

In [6]:
response

ChatCompletion(id='chatcmpl-ABi2p3UVxGbEpuKdCtxaWOcI1YAD9', choices=[Choice(finish_reason='stop', index=0, logprobs=None, message=ChatCompletionMessage(content="Superman's weakness is Kryptonite, a radioactive mineral from his home planet of Krypton. Exposure to Kryptonite weakens Superman and can even kill him. Other weaknesses of Superman include red solar radiation, which drains his powers, and magic, which can bypass his invulnerability.", role='assistant', function_call=None, tool_calls=None, refusal=None))], created=1727354279, model='gpt-3.5-turbo-0125', object='chat.completion', system_fingerprint=None, usage=CompletionUsage(completion_tokens=59, prompt_tokens=13, total_tokens=72, completion_tokens_details={'reasoning_tokens': 0}))

Which produces the expected response

In [7]:
response.choices[0].message

ChatCompletionMessage(content="Superman's weakness is Kryptonite, a radioactive mineral from his home planet of Krypton. Exposure to Kryptonite weakens Superman and can even kill him. Other weaknesses of Superman include red solar radiation, which drains his powers, and magic, which can bypass his invulnerability.", role='assistant', function_call=None, tool_calls=None, refusal=None)

In [8]:
response.choices[0].message.content

"Superman's weakness is Kryptonite, a radioactive mineral from his home planet of Krypton. Exposure to Kryptonite weakens Superman and can even kill him. Other weaknesses of Superman include red solar radiation, which drains his powers, and magic, which can bypass his invulnerability."

### Multiple alternatives

To request multiple answers, we must include the `n` parameter with the number of answers we want

In [9]:
%%time
response = client.chat.completions.create(
    model="gpt-3.5-turbo",
    messages=[
        {"role": "user", 
         "content": "What are the different kinds of Kryptonite?"},
    ],
    n=3
)

CPU times: user 5.86 ms, sys: 2.25 ms, total: 8.11 ms
Wall time: 6.52 s


And we can access each of the answers individually int he choices list

In [10]:
for output in response.choices:
    print("==========")
    print(output.message.role.title()) 
    print("==========")
    print(output.message.content)
    print("==========\n")

Assistant
There are several different types of Kryptonite in the DC Comics universe, each with its own unique effects on the character Superman:

1. Green Kryptonite - The most well-known form of Kryptonite, green Kryptonite weakens Superman and can eventually kill him if he is exposed to it for an extended period of time.

2. Red Kryptonite - Red Kryptonite has unpredictable and temporary effects on Superman, often altering his personality or physical abilities in strange ways.

3. Blue Kryptonite - Blue Kryptonite is harmless to Superman, but deadly to Bizarro, a flawed clone of Superman.

4. Gold Kryptonite - Gold Kryptonite permanently removes Superman's powers, leaving him permanently vulnerable to harm.

5. Black Kryptonite - Black Kryptonite can split Superman into two separate beings, representing his good and evil sides.

6. White Kryptonite - White Kryptonite is lethal to plant life from Krypton, but harmless to Superman.

7. Pink Kryptonite - In one comic storyline, pink Kry

### Language Translation

In [11]:
response = client.chat.completions.create(
    model='gpt-3.5-turbo',
    messages=[{"role": "system", "content": "You're a professional English-Italian translator."}, 
              {"role": "user", "content": "Translate 'Be the change that you wish to see in the world.' into Italian"}],
    temperature=0,
)

In [12]:
response.choices[0].message.content

'"Sii il cambiamento che desideri vedere nel mondo."'

### Image generation

In [13]:
prompt = "A wimsical image of a toy duck with an eye patch and hat floating in the clouds"

In [14]:
%%time
response = client.images.generate(
    model="dall-e-2",
    prompt=prompt,
    n=1,
    size="1024x1024",
    response_format="url",
)

CPU times: user 5.54 ms, sys: 2.36 ms, total: 7.9 ms
Wall time: 10.9 s


In [15]:
response

ImagesResponse(created=1727354298, data=[Image(b64_json=None, revised_prompt=None, url='https://oaidalleapiprodscus.blob.core.windows.net/private/org-cEu7KbLexcTF7u2YnTgg3tFV/user-OYeHJ0J19d8sU7MeuMaFfyf7/img-JeyY8YIdPGwl2JsFLaqENUGs.png?st=2024-09-26T11%3A38%3A18Z&se=2024-09-26T13%3A38%3A18Z&sp=r&sv=2024-08-04&sr=b&rscd=inline&rsct=image/png&skoid=d505667d-d6c1-4a0a-bac7-5c84a87759f8&sktid=a48cca56-e6da-484e-a814-9c849652bcb3&skt=2024-09-25T23%3A26%3A33Z&ske=2024-09-26T23%3A26%3A33Z&sks=b&skv=2024-08-04&sig=nKG6zWo6xg6d9Xv8/NJcmw7ad6DZsZ3GG/VnXmst4Qw%3D')])

Utility function to download the image

In [16]:
def download_file(url, filename):
    with requests.get(url, stream=True) as r:
        total_length = int(r.headers.get("Content-Length"))
        with tqdm.wrapattr(r.raw, "read", total=total_length, desc=filename) as raw:
            with open(filename, 'wb')as output:
                shutil.copyfileobj(raw, output)

In [17]:
image_dir = 'images/'

In [18]:
image_url = response.data[0].url

In [19]:
print(image_url)

https://oaidalleapiprodscus.blob.core.windows.net/private/org-cEu7KbLexcTF7u2YnTgg3tFV/user-OYeHJ0J19d8sU7MeuMaFfyf7/img-JeyY8YIdPGwl2JsFLaqENUGs.png?st=2024-09-26T11%3A38%3A18Z&se=2024-09-26T13%3A38%3A18Z&sp=r&sv=2024-08-04&sr=b&rscd=inline&rsct=image/png&skoid=d505667d-d6c1-4a0a-bac7-5c84a87759f8&sktid=a48cca56-e6da-484e-a814-9c849652bcb3&skt=2024-09-25T23%3A26%3A33Z&ske=2024-09-26T23%3A26%3A33Z&sks=b&skv=2024-08-04&sig=nKG6zWo6xg6d9Xv8/NJcmw7ad6DZsZ3GG/VnXmst4Qw%3D


In [20]:
image_filename = os.path.join(image_dir, 'ducky.png')
download_file(image_url, image_filename)

images/ducky.png:   0%|          | 0/3147981 [00:00<?, ?it/s]

In [21]:
Image(filename=image_filename)

# HuggingFace

In [22]:
unmasker = pipeline('fill-mask', model='bert-base-uncased')

Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertForMaskedLM: ['bert.pooler.dense.bias', 'bert.pooler.dense.weight', 'cls.seq_relationship.bias', 'cls.seq_relationship.weight']
- This IS expected if you are initializing BertForMaskedLM from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForMaskedLM from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


In [23]:
unmasker("Artificial Intelligence [MASK] take over the world.")

[{'score': 0.31824299693107605,
  'token': 2064,
  'token_str': 'can',
  'sequence': 'artificial intelligence can take over the world.'},
 {'score': 0.18299730122089386,
  'token': 2097,
  'token_str': 'will',
  'sequence': 'artificial intelligence will take over the world.'},
 {'score': 0.0560012087225914,
  'token': 2000,
  'token_str': 'to',
  'sequence': 'artificial intelligence to take over the world.'},
 {'score': 0.045194774866104126,
  'token': 2015,
  'token_str': '##s',
  'sequence': 'artificial intelligences take over the world.'},
 {'score': 0.045152731239795685,
  'token': 2052,
  'token_str': 'would',
  'sequence': 'artificial intelligence would take over the world.'}]

### Question answering

In [24]:
text = """Dear Amazon, last week I ordered an Optimus Prime action figure \
from your online store in Germany. Unfortunately, when I opened the package, \
I discovered to my horror that I had been sent an action figure of Megatron \
instead! As a lifelong enemy of the Decepticons, I hope you can understand my \
dilemma. To resolve the issue, I demand an exchange of Megatron for the \
Optimus Prime figure I ordered. Enclosed are copies of my records concerning \
this purchase. I expect to hear from you soon. Sincerely, Bumblebee."""

In [25]:
reader = pipeline("question-answering")

No model was supplied, defaulted to distilbert/distilbert-base-cased-distilled-squad and revision 626af31 (https://huggingface.co/distilbert/distilbert-base-cased-distilled-squad).
Using a pipeline without specifying a model name and revision in production is not recommended.
/opt/anaconda3/lib/python3.11/site-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(


In [26]:
question = "What does the customer want?"

In [27]:
outputs = reader(question=question, context=text)
pd.DataFrame([outputs])    

score  start  end                   answer
0  0.631292    335  358  an exchange of Megatron

### Named Entity Recognition

In [28]:
ner_tagger = pipeline("ner", aggregation_strategy="simple")
outputs = ner_tagger(text)
pd.DataFrame(outputs)    

No model was supplied, defaulted to dbmdz/bert-large-cased-finetuned-conll03-english and revision f2482bf (https://huggingface.co/dbmdz/bert-large-cased-finetuned-conll03-english).
Using a pipeline without specifying a model name and revision in production is not recommended.
/opt/anaconda3/lib/python3.11/site-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(
Some weights of the model checkpoint at dbmdz/bert-large-cased-finetuned-conll03-english were not used when initializing BertForTokenClassification: ['bert.pooler.dense.bias', 'bert.pooler.dense.weight']
- This IS expected if you are initializing BertForTokenClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTra

entity_group     score           word  start  end
0          ORG  0.879010         Amazon      5   11
1         MISC  0.990859  Optimus Prime     36   49
2          LOC  0.999755        Germany     90   97
3         MISC  0.556572           Mega    208  212
4          PER  0.590255         ##tron    212  216
5          ORG  0.669693         Decept    253  259
6         MISC  0.498348        ##icons    259  264
7         MISC  0.775362       Megatron    350  358
8         MISC  0.987854  Optimus Prime    367  380
9          PER  0.812097      Bumblebee    502  511

<center>
     <img src="data/D4Sci_logo_full.png" alt="Data For Science, Inc" align="center" border="0" width=300px> 
</center>